In [1]:
import pandas as pd
import sklearn
import fastparquet
dnsdata=pd.read_parquet('/stuff/dnsdata')

pd.set_option('display.max_columns', None)  
pd.set_option('display.max_rows', None) 
pd.set_option('display.max_colwidth', -1)

In [146]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
subset=dnsdata[['benign','A']]

In [3]:
def ipcleanup(row):
    iprow=[]
    for address in row['A']:
        try:
            tempstring=address.split('IN A')
            iprow.append(tempstring[1].strip())
        except IndexError:  
            pass
    row['A']=iprow
    return row    

def ttlcleanup(row):
    ttlrow=[]
    for address in row['A']:
        try:
            tempdata=address.split('IN A')
            tempdata2=tempdata[0].split(' ')
            ttlrow.append(tempdata2[1])
        except IndexError:
            pass
    row['A']=ttlrow
    return row
            
ipdata=subset.apply(ipcleanup,axis='columns')
ttldata=subset.apply(ttlcleanup,axis='columns')

In [4]:
cleaneripdata=ipdata[ipdata['A'].map(lambda x: len(x)>0)]


benign  \
254600  True     
28463   False    
161036  False    
53165   False    
38877   False    
34671   True     
65722   False    
111010  True     
92512   True     
162212  True     
124985  False    
183827  True     
227790  True     
204803  False    
268012  True     
286424  False    
268966  False    
66115   False    
43145   True     
88571   False    
224684  False    
179216  False    
1287    False    
75316   True     
252803  False    
131842  True     
76563   False    
236216  False    
95483   True     
150393  False    
161808  False    
119081  False    
180230  False    
250087  False    
274942  False    
264085  True     
265863  True     
155594  True     
231513  True     
260870  False    
195210  False    
164693  False    
253058  True     
154145  True     
159531  True     
236812  False    
48379   True     
42773   True     
83644   False    
288928  False    
174540  False    
146775  False    
235938  False    
148177  False    
166047  False    
111631  False    
177065  False    
148438  False    
107054  False    
268144  True     
57070   False    
5081    False    
269195  False    
57369   False    
110065  False    
29956   False    
90162   False    
257789  False    
249324  False    
235383  True     
249197  True     
275899  False    
177223  True     
76864   False    
210287  False    
56303   False    
110243  True     
39941   False    
290302  True     
54195   True     
260493  False    
64868   True     
186643  False    
197333  True     
283484  True     
215686  True     
4669    False    
109052  False    
182268  True     
195573  False    
239366  False    
241962  False    
47541   False    
225787  True     
265728  True     
106556  False    
166498  False    
159959  True     
274536  False    
143711  False    

                                                                                                  A  
254600  [93.93.51.223]                                                                               
28463   [159.127.187.12]                                                                             
161036  [69.10.55.96]                                                                                
53165   [104.16.155.36, 104.16.154.36]                                                               
38877   [0.0.0.0]                                                                                    
34671   [72.163.4.185]                                                                               
65722   [208.100.26.251]                                                                             
111010  [104.20.86.213, 104.20.87.213]                                                               
92512   [210.189.86.12]                                                                              
162212  [82.165.229.138, 82.165.230.17]                                                              
124985  [185.87.187.198]                                                                             
183827  [104.20.114.3, 104.20.115.3]                                                                 
227790  [171.67.215.200]                                                                             
204803  [104.24.117.146, 104.24.116.146]                                                             
268012  [216.58.215.67]                                                                              
286424  [107.180.41.154]                                                                             
268966  [107.180.57.10]                                                                              
66115   [91.194.40.148]                                                                              
43145   [192.0.72.2]                                                                                 
88571   [198.54.116.169]                                                                             
224684  [47.75.92.180]                         

In [16]:
#TODO: find a more reliable/thorough database to use
import geoip2.database
reader=geoip2.database.Reader('/stuff/geolite data/GeoLite2-City.mmdb')
geodata=pd.DataFrame()
def getplotdata(row):
    geodata=[]
    for data in row['A']:
        print(data)
        try:
            response=reader.city(data)
            geodata.insert(0,[response.country.name,response.city.name])
        except Exception:
            geodata=[]
    row=geodata
    return row

geodata=cleaneripdata.apply(getplotdata,axis='columns')


64.6.231.77
43.245.53.42
159.69.121.73
203.157.65.4
119.47.118.96
43.245.53.42
203.157.65.4
64.6.231.77
159.69.121.73
119.47.118.96
172.245.13.172
49.50.249.70
49.50.249.70
49.50.249.70
49.50.249.70
203.96.152.15
192.99.151.130
185.33.54.7
203.96.152.15
192.99.151.130
185.33.54.7
103.49.205.15
119.47.118.22
103.49.205.15
119.47.118.22
67.225.191.184
145.239.70.100
89.46.107.25
104.244.127.3
70.32.23.15
93.158.208.46
118.67.248.229
103.250.232.40
207.174.214.206
103.49.205.15
208.91.197.160
195.162.24.206
173.212.215.250
13.237.7.255
184.95.44.219
184.95.44.219
49.51.154.155
67.225.191.184
145.239.70.100
89.46.107.25
104.244.127.3
119.47.118.96
43.245.53.42
43.245.53.42
43.245.53.42
93.158.208.46
212.33.77.182
103.250.232.40
103.49.205.15
208.91.197.160
195.162.24.206
13.237.7.255
184.95.44.219
49.51.154.155
192.3.194.16
192.3.194.16
192.3.194.16
192.3.194.16
70.32.23.15
118.67.248.229
192.3.194.16
192.3.194.16
192.3.194.16
207.174.214.206
192.3.194.16
173.212.215.250
184.95.44.219
192.

78.8.195.212
78.8.195.212
62.129.238.44
162.208.0.242
34.239.161.8
62.129.219.152
103.14.97.150
199.241.186.126
35.184.61.254
162.241.5.182
108.61.147.50
154.0.165.111
103.86.176.148
154.0.164.179
103.18.6.212
66.7.217.68
109.237.24.148
201.148.104.80
81.88.48.97
81.171.31.230
198.38.82.69
195.201.242.71
149.210.209.183
69.163.232.190
162.241.209.218
209.222.108.146
137.74.93.14
37.9.175.26
198.50.224.50
149.154.66.110
68.66.249.105
188.165.246.203
89.43.66.107
89.43.66.107
192.169.80.2
52.59.86.123
185.12.108.116
149.255.62.32
194.28.84.212
191.5.59.14
187.95.224.86
146.185.160.62
154.0.172.79
95.179.133.78
98.129.229.226
35.231.137.207
130.185.87.16
178.62.174.174
186.202.161.190
110.170.168.217
103.18.6.211
103.81.85.79
162.244.93.206
78.153.216.8
185.68.16.136
138.201.142.125
125.65.113.111
42.112.30.38
202.155.223.18
203.113.135.194
81.177.140.11
188.134.71.31
79.96.82.126
184.107.39.4
73.140.45.63
73.140.45.63
91.217.9.188
159.203.48.32
202.52.147.103
46.4.81.203
54.94.151.4
52.5

217.26.54.189
217.26.54.189
217.26.54.189
217.26.54.189
198.98.62.207
31.177.78.16
80.74.149.162
198.98.62.207
31.177.78.16
185.52.2.154
78.46.77.98
83.137.114.198
213.186.33.5
217.26.55.5
104.31.72.20
104.31.73.20
104.24.23.22
104.24.22.22
80.74.145.65
80.74.144.93
185.52.2.154
217.26.53.161
136.243.13.215
80.244.187.247
185.51.191.29
94.126.23.52
217.26.53.37
185.52.2.154
173.212.202.129
217.26.52.10
217.26.54.189
136.243.162.140
83.138.82.107
83.166.138.7
13.57.63.201
162.255.119.157
162.255.119.122
114.248.80.75
199.247.25.110
192.64.119.26
192.64.119.176
202.182.108.174
108.61.197.172
45.32.53.250
43.248.10.160
45.32.53.250
202.182.108.174
45.32.53.250
127.0.0.1
59.188.196.162
218.32.21.212
198.54.117.197
198.54.117.198
198.54.117.199
198.54.117.200
209.99.40.223
23.107.124.207
183.236.2.18
183.236.2.18
192.185.46.44
153.92.0.100
193.109.246.62
144.76.162.245
35.231.151.7
35.229.93.46
208.100.26.251
209.99.40.219
193.146.253.39
192.42.119.41
199.2.137.29
34.76.231.175
199.2.137.29

162.241.203.111
104.31.72.250
104.31.73.250
52.34.25.27
187.108.203.101
61.93.220.165
104.248.112.102
185.165.123.4
115.112.176.19
104.37.86.29
78.108.93.83
87.110.219.224
185.35.138.221
185.165.123.4
203.66.168.117
54.214.100.220
192.162.70.139
52.206.191.20
54.233.222.199
196.38.40.86
162.241.203.111
91.195.240.126
122.10.96.61
104.31.73.250
104.31.72.250
52.34.25.27
62.210.177.105
192.168.1.128
141.255.151.152
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
175.126.123.219
64.95.103.184
173.231.184.55
157.122.62.194
157.122.62.194
157.122.62.194
46.101.128.59
157.122.62.194
157.122.62.194
157.122.62.194
15

50.87.150.147
104.27.172.74
104.27.184.112
104.201.21.134
104.24.115.59
5.2.78.11
104.18.50.36
104.27.128.94
104.24.98.93
104.27.165.34
104.27.142.41
184.168.221.91
192.232.216.117
104.31.66.85
104.28.19.46
104.28.5.182
107.180.34.197
192.254.228.240
192.232.216.117
192.232.216.117
192.232.216.117
107.180.34.197
107.180.34.197
107.180.34.197
192.254.228.240
192.254.228.240
192.254.228.240
79.170.40.41
185.117.155.106
104.27.128.83
185.66.9.184
185.117.155.106
104.27.174.205
5.2.78.11
192.254.250.243
104.18.43.111
45.60.25.49
45.60.22.49
185.117.155.106
79.170.40.41
79.170.40.41
79.170.40.41
185.117.155.106
185.117.155.106
185.117.155.106
185.66.9.184
185.66.9.184
185.66.9.184
185.117.155.106
185.117.155.106
185.117.155.106
192.254.250.243
192.254.250.243
192.254.250.243
45.60.22.49
45.60.25.49
45.60.25.49
45.60.22.49
45.60.22.49
45.60.25.49
185.117.155.106
185.117.155.106
185.66.9.184
104.27.145.104
85.214.79.138
192.185.17.120
185.117.155.106
104.28.5.18
192.185.35.44
205.178.189.129


...

208.91.197.27
141.105.71.48
185.234.218.247
154.86.2.138
115.231.73.12
115.238.185.43
103.204.179.26
221.229.162.116
125.65.112.193
103.115.41.146
103.115.41.146
43.242.75.67
91.21.140.182
184.168.221.55
205.134.171.68
153.92.0.100
213.202.229.103
153.92.0.100
88.198.231.1
153.92.0.100
213.202.229.103
81.177.141.131
138.201.53.141
153.92.0.100
91.195.240.126
153.92.0.100
104.243.41.186
95.211.16.66
185.176.27.149
185.224.138.172
217.8.117.5
185.120.222.2
200.63.45.123
104.152.168.30
185.176.27.149
95.215.1.196
95.215.1.196
104.28.2.158
185.20.185.158
49.51.84.234
47.91.41.254
185.158.249.240
185.62.189.68
176.57.69.73
103.214.6.170
181.174.165.164
217.147.169.71
95.179.187.196
185.212.129.227
80.67.17.210
91.195.240.117
213.226.68.93
77.221.144.122
109.196.164.18
192.64.119.152
185.84.181.83
195.24.66.145
194.67.197.64
5.253.61.186
85.143.173.222
5.101.88.38
194.67.198.138
192.145.99.61
85.143.173.0
47.254.16.142
176.105.252.171
195.133.196.167
194.67.211.105
47.254.16.142
47.254.135.1

204.135.13.50
204.135.8.175
204.135.13.175
204.135.8.155
151.101.66.133
151.101.194.133
151.101.2.133
151.101.130.133
104.20.42.23
104.20.41.23
188.72.213.220
188.72.213.221
213.215.199.52
35.186.213.112
176.53.59.98
176.53.59.96
176.53.59.97
172.241.24.65
172.241.24.22
169.44.67.232
169.44.67.231
50.22.67.98
172.241.24.20
172.241.24.66
169.44.67.161
75.126.123.82
169.46.246.6
91.204.210.226
151.101.1.164
151.101.193.164
151.101.129.164
151.101.65.164
13.224.96.19
13.224.96.14
13.224.96.116
13.224.96.77
69.172.201.47
134.213.233.164
45.249.212.124
212.42.76.253
212.42.76.252
61.152.229.228
203.130.48.144
203.130.48.145
52.94.237.126
52.94.226.87
54.239.26.220
129.176.217.220
200.44.45.12
185.147.178.11
185.147.178.14
185.147.178.12
185.147.178.13
60.12.149.194
216.18.168.1
104.20.135.55
104.20.134.55
195.211.221.116
104.18.95.72
104.18.94.72
68.233.77.233
104.31.83.165
104.31.82.165
35.186.243.87
109.236.84.187
109.236.84.191
109.236.92.168
109.236.92.167
217.23.13.58
217.23.13.46
104.

79.175.141.112
216.58.211.35
51.254.235.119
80.247.32.208
36.110.213.49
185.37.100.123
92.122.19.146
104.17.14.48
104.16.176.44
94.23.144.230
192.243.54.98
104.17.160.54
104.17.159.54
115.238.23.240
140.205.77.240
208.109.192.71
103.49.221.130
203.190.242.254
113.217.247.100
104.16.92.22
104.16.93.22
104.20.9.120
104.20.10.120
216.18.168.116
216.151.17.140
83.206.67.137
172.217.17.4
144.160.36.42
144.160.155.43
216.58.201.131
72.163.4.185
99.86.88.23
99.86.88.29
99.86.88.107
99.86.88.98
94.124.200.0
3.122.27.66
3.122.74.177
18.185.190.51
180.101.45.119
127.0.0.1
198.134.112.242
198.134.112.241
198.134.112.243
198.134.112.244
162.125.248.1
104.25.71.103
104.25.72.103
172.217.17.3
23.223.92.168
104.28.18.156
104.28.19.156
54.254.244.247
13.229.167.151
159.180.84.9
94.102.53.113
194.50.69.124
91.211.75.124
107.182.230.211
185.80.221.89
185.80.220.71
107.182.230.212
169.63.74.83
185.80.220.72
169.55.100.68
66.135.195.175
66.135.196.249
35.200.167.142
104.31.17.3
104.31.16.3
185.129.44.23
1

104.16.105.87
104.16.204.58
216.58.207.67
151.101.2.114
151.101.66.114
151.101.130.114
151.101.194.114
104.27.217.28
104.27.216.28
13.90.213.204
52.165.129.203
216.21.13.12
216.21.13.13
104.16.91.52
104.16.92.52
125.209.214.79
104.16.168.99
104.17.136.89
223.165.27.146
213.209.17.209
35.155.180.173
34.212.55.67
43.245.43.18
2.18.66.41
2.18.66.57
196.205.93.110
205.201.132.96
113.107.236.195
221.228.79.225
47.98.19.216
112.74.137.42
118.25.31.186
14.17.109.66
113.107.236.195
157.240.18.35
2.22.139.187
208.109.192.70
104.25.101.115
104.25.102.115
206.54.165.186
188.72.213.176
188.42.162.184
188.42.162.170
188.72.213.175
35.186.248.227
212.27.48.10
104.98.128.99
172.217.168.35
141.101.120.55
141.101.120.54
185.44.0.36
185.44.0.16
185.44.0.26
145.239.9.15
185.134.201.6
185.134.201.5
185.134.203.243
185.134.203.245
111.161.64.40
111.161.64.48
123.126.157.222
123.126.55.41
204.79.197.212
88.221.134.185
88.221.134.243
74.113.237.64
104.17.139.178
104.17.141.178
104.17.138.178
104.17.137.178
1

217.160.0.208
81.92.202.161
83.223.101.76
163.172.24.64
212.83.158.223
134.119.253.108
89.252.190.48
209.99.16.222
103.17.8.47
8.209.75.192
166.62.108.43
149.56.43.78
144.217.72.25
77.104.144.20
92.53.96.184
178.77.86.131
41.231.120.145
199.188.203.224
109.68.33.25
46.43.34.31
220.118.44.208
198.54.112.26
212.83.61.220
51.77.74.174
88.208.252.9
49.51.155.69
173.255.241.171
23.105.131.151
103.136.43.131
52.41.3.203
23.96.39.148
35.163.175.186
116.203.61.78
141.8.195.21
185.244.29.8
216.146.43.71
162.88.193.70
216.146.43.70
131.186.113.70
23.101.123.81
41.203.78.204
142.44.131.79
185.52.2.154
199.192.22.155
23.105.131.147
91.193.75.29
104.27.142.252
104.27.143.252
52.55.120.73
103.200.6.79
190.84.167.75
52.6.79.229
34.233.102.38
18.211.215.84
52.202.139.131
52.206.161.133
52.200.125.74
80.237.133.179
104.24.1.72
104.24.0.72
185.244.29.223
69.163.220.39
185.255.55.29
37.128.147.83
192.185.211.163
92.43.109.201
192.169.69.25
212.100.94.223
185.244.31.24
199.192.16.126
194.30.35.117
185.19.

In [18]:
geodata.sample(100)

146771    [[Netherlands, None]]                                                                                                                                                                                           
220510    [[Ireland, Dublin], [Ireland, Dublin]]                                                                                                                                                                          
16393     [[United States, Scottsdale]]                                                                                                                                                                                   
216137    [[Hong Kong, None]]                                                                                                                                                                                             
250253    [[Turkey, Istanbul]]                                                                                              

In [16]:
badgps=geodata[geodata['benign']==False]
goodgps=geodata[geodata['benign']==True]

In [20]:
putitalltogether=ipdata.copy()
putitalltogether.insert(1,'geodata',geodata)
putitalltogether.insert(1,'ttl',ttldata['A'])

In [9]:
putitalltogether.to_parquet('ipaddressdata')

In [21]:
putitalltogether.sample(100)

benign                                                 ttl  \
285077  False   [49, 49, 49]                                         
150059  False   [Nameservers]                                        
110395  True    [119]                                                
188240  True    [15]                                                 
51377   True    [59]                                                 
14985   False   [210]                                                
130573  True    [299]                                                
112122  False   [1357]                                               
168941  False   [3769]                                               
134424  True    [250, 250, 250, 250, 250]                            
244173  False   [12603]                                              
94544   False   [299]                                                
64119   True    [3, 3, 3]                                            
225003  True    [29, 29]                                             
104627  True    [3124]                                               
26437   False   [599]                                                
18331   False   [Nameservers]                                        
116774  False   [7381]                                               
140943  False   [59]                                                 
49520   True    [285, 285, 285]                                      
82192   True    [59, 59, 59]                                         
287103  False   [1796]                                               
109727  False   [599]                                                
270803  True    [251]                                                
32108   True    [511]                                                
7947    False   [3599]                                               
243987  True    [59]                                                 
202436  False   [296, 296]                                           
74688   True    [299]                                                
77777   True    [59, 59, 59, 59]                                     
52088   True    [90]                                                 
23445   False   [3599]                                               
230052  False   [665]                                                
113872  False   [3590]                                               
49715   True    [299, 299]                                           
128262  False   [299, 299]                                           
246989  False   [149]                                                
181123  False   [14399]                                              
130408  True    [59, 59, 59, 59]                                     
170702  False   [299]                                                
251230  False   [21599]                                              
78113   True    [172, 172]                                           
22771   False   [3599]                                               
266606  False   [599]                                                
159518  True    [599, 599, 599]                                      
255038  True    [42, 42, 42, 42]                                     
256482  False   [599]                                                
259854  True    [226]                                                
43891   False   [320]                                                
24549   False   [4]                                                  
155313  True    [9]                                                  
36768   True    [1929]                                               
62991   False   [3599]                                               
1529    False   [Answer]                                             
20478   False   [3599]                                               
49453   True    [299, 299, 299, 299, 299, 299, 299, 299, 299, 299]   
279953  False   [5